In [7]:
# !pip install simpletransformers

# Modelling

Created a NER dataset using the notebook ner-data-preparation.ipynb, after running on this notebook, we get two csv files train.csv and test.csv

In [ ]:
import numpy as np
import pandas as pd
import os
# for dirname, _, filenames in os.walk('/kaggle/input'):
#     for filename in filenames:
#         print(os.path.join(dirname, filename))


In [ ]:
import pandas as pd
import numpy as np
from tqdm import tqdm, trange
# data = pd.read_csv("/content/drive/MyDrive/publicis/train.csv").fillna(method="ffill")
# data.tail(10)

train = pd.read_csv("/content/drive/MyDrive/publicis/train.csv", encoding='unicode_escape')
test = pd.read_csv("/content/drive/MyDrive/publicis/test.csv", encoding='unicode_escape')
data = pd.concat([train, test], axis=0)
data.shape

(35137, 4)

In [ ]:
data.head()

Unnamed: 0  sent_id   text       tag
0           0      792    Has         O
1           1      792    the         O
2           2      792   chef  B-ASPECT
3           3      792    and         O
4           4      792  owner  B-ASPECT

In [ ]:
test_sentence = " ".join(test[test["sent_id"]==1386]["text"].tolist())

# Term NERTraining

In [ ]:
import pandas as pd
import numpy as np
from tqdm import tqdm, trange
from simpletransformers.ner import NERModel, NERArgs

# data = pd.read_csv("/content/drive/MyDrive/publicis/train.csv").fillna(method="ffill")
# data.tail(10)

train = pd.read_csv("/content/drive/MyDrive/publicis/train.csv", encoding='unicode_escape')
test = pd.read_csv("/content/drive/MyDrive/publicis/test.csv", encoding='unicode_escape')
data = pd.concat([train, test], axis=0)
data.shape

(35137, 4)

Renaming the columns to train using simple transformers

In [ ]:
train  = train.rename(columns={"sent_id": "sentence_id", "text": "words", "tag": "labels"})
test  = test.rename(columns={"sent_id": "sentence_id", "text": "words", "tag": "labels"})

In [ ]:
train.shape, test.shape

((24571, 4), (10566, 4))

Removing the sentences having tag "-".

In [ ]:
train_issues = set(train[train["labels"]== "-"]["sentence_id"].tolist())
test_issues = set(test[test["labels"]== "-"]["sentence_id"].tolist())


In [ ]:
new_train = train[~train["sentence_id"].isin(train_issues)]
new_test = test[~test["sentence_id"].isin(test_issues)]

In [ ]:
new_train.shape, new_test.shape

((24504, 4), (10480, 4))

In [ ]:
new_train["labels"].value_counts()

labels
O           20930
B-ASPECT     2526
I-ASPECT     1048
Name: count, dtype: int64

In [ ]:
new_test["labels"].value_counts()

labels
O           8840
B-ASPECT    1150
I-ASPECT     490
Name: count, dtype: int64

### NER Training

In [ ]:


model_args = NERArgs()
model_args.labels_list = ["O", "B-ASPECT", "I-ASPECT"]

args={"save_eval_checkpoints": False,
      "save_steps": -1,
      "output_dir": "/content/drive/MyDrive/publicis/combined_ner",
      'overwrite_output_dir': True,
      "save_model_every_epoch": False,
      #'reprocess_input_data': True,
      "labels_list" :["O", "B-ASPECT", "I-ASPECT"],
      'learning_rate': 5e-5,
      "train_batch_size": 16,'num_train_epochs': 12,"max_seq_length": 256, "gradient_accumulation_steps": 8}
model = NERModel(
    "distilbert",
    "dslim/distilbert-NER",
    labels=["O", "B-ASPECT", "I-ASPECT"],
    args=args, ignore_mismatched_sizes=True
)

Some weights of DistilBertForTokenClassification were not initialized from the model checkpoint at dslim/distilbert-NER and are newly initialized because the shapes did not match:
- classifier.bias: found shape torch.Size([9]) in the checkpoint and torch.Size([3]) in the model instantiated
- classifier.weight: found shape torch.Size([9, 768]) in the checkpoint and torch.Size([3, 768]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [6]:
#Training the Model
from sklearn.metrics import accuracy_score, f1_score
model.train_model(new_train,eval_data = new_test,acc=f1_score)

### NER Model Evaluation on test set

In [ ]:
#Evaluating the Model
result, model_outputs, preds_list = model.eval_model(new_test)
print(result)

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/7 [00:00<?, ?it/s]

{'eval_loss': 0.12246257607226393, 'precision': 0.8410819949281487, 'recall': 0.8652173913043478, 'f1_score': 0.8529789969995712}


We achieved an **F1-score of 85%** for term token classification. As this is the base model, we can look for improvements in f1-score

## Loading Trained Term NERModel

In [ ]:
model1 = NERModel(
    "distilbert",
    "/content/drive/MyDrive/publicis/combined_ner",
    labels=["O", "B-ASPECT", "I-ASPECT"],
    args=args, ignore_mismatched_sizes=True
)

NameError: name 'args' is not defined

In [ ]:
test_sentence = """
The food 's dazzling flavors overwhelm the palate , truly embracing the beauty of authentic Thai cuisine .
"""
model1.predict([test_sentence])

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

([[{'The': 'O'},
   {'food': 'B-ASPECT'},
   {"'s": 'O'},
   {'dazzling': 'O'},
   {'flavors': 'B-ASPECT'},
   {'overwhelm': 'O'},
   {'the': 'O'},
   {'palate': 'O'},
   {',': 'O'},
   {'truly': 'O'},
   {'embracing': 'O'},
   {'the': 'O'},
   {'beauty': 'O'},
   {'of': 'O'},
   {'authentic': 'O'},
   {'Thai': 'B-ASPECT'},
   {'cuisine': 'I-ASPECT'},
   {'.': 'O'}]],
 [[{'The': [[6.633, -3.33, -3.617]]},
   {'food': [[-2.396, 5.13, -3.273]]},
   {"'s": [[5.473, -3.953, -1.616], [6.1, -3.89, -2.408]]},
   {'dazzling': [[6.19, -3.143, -3.441], [5.98, -2.94, -3.293]]},
   {'flavors': [[-1.452, 3.0, -2.725], [5.008, -3.62, -1.376]]},
   {'overwhelm': [[6.566, -3.316, -3.29],
     [6.523, -3.299, -3.35],
     [6.52, -3.383, -3.193],
     [6.652, -3.355, -3.252]]},
   {'the': [[6.688, -3.049, -3.586]]},
   {'palate': [[3.404, 1.334, -4.977],
     [3.832, 0.3105, -4.25],
     [3.574, -0.6353, -3.486]]},
   {',': [[6.72, -3.416, -3.277]]},
   {'truly': [[6.625, -3.25, -3.473]]},
   {'embracin

# Model Building for Aspect Term Polarity

Using the below code, we are extracting the data from xml, we get two outputs one a dataframe with all the info in a single table. Other is a list of terms in a given sentence and list of categories mentioned for a unique sentence.

In [ ]:
import xml.etree.ElementTree as ET
import pandas as pd
tree = ET.parse('/content/drive/MyDrive/publicis/Restaurants_Train_v2.xml')
root = tree.getroot()
# Parse the XML data
# root = ET.fromstring(xml_data)
# Function to extract positions

def extract_positions(root):
    data = []
    aspect_term_cat_list = []
    sentences = root.findall('sentence')
    for sentence in sentences:
        new_dict = {}
        sentence_id = sentence.get('id')
        text = sentence.find('text').text
        new_dict["sentence_id"] = sentence_id
        new_dict["text"] = text
        new_dict["aspectTerms"] = []
        new_dict["aspectCategory"] = []
        d = [sentence_id, text]

        aspect_terms = sentence.find('aspectTerms')
        aspect_terms_list_sent = []
        if aspect_terms is not None:

            for aspect_term in aspect_terms.findall('aspectTerm'):
                aspect_term_dict = {}
                term = aspect_term.get('term')
                term_from = int(aspect_term.get('from', 0))
                term_to = int(aspect_term.get('to', 0))
                polarity = aspect_term.get('polarity')

                aspect_term_dict["term"] = term
                aspect_term_dict["term_from"] = term_from
                aspect_term_dict["term_to"] = term_to
                aspect_term_dict["polarity"] = polarity
                data.append( d + [term, term_from, term_to, polarity, "", ""])
                new_dict["aspectTerms"].append(aspect_term_dict)
                aspect_terms_list_sent.append(term)
                # print(f"Sentence ID: {sentence_id}, Term: '{term}', Start: {term_from}, End: {term_to}, Polarity: {polarity}")

        aspect_categories = sentence.find('aspectCategories')
        aspect_categ_list_sent = []
        if aspect_categories is not None:
            for aspect_category in aspect_categories.findall('aspectCategory'):
                aspect_cat_dict = {}
                category = aspect_category.get('category')
                polarity = aspect_category.get('polarity')

                aspect_cat_dict["category"] = category
                aspect_cat_dict["polarity"] = polarity

                data.append( d + ["", 0, 0, "", category, polarity])
                new_dict["aspectCategory"].append(aspect_cat_dict)
                aspect_categ_list_sent.append(category)

                # For categories, we're not given start and end positions, so we consider the entire sentence.
                # print(f"Sentence ID: {sentence_id}, Category: '{category}', Polarity: {polarity}, Text: '{text}'")
        aspect_term_cat_list.append((int(sentence_id), text, aspect_terms_list_sent, aspect_categ_list_sent))
        # data.append(new_dict)
    columns = ["sent_id", "text", "term", "term_from", "term_to", "term_polarity", "category", "category_polarity"]
    df =  pd.DataFrame(data, columns=columns)
    return df, aspect_term_cat_list

In [ ]:
# Call the function
data, aspect_term_cat_list = extract_positions(root)
data["sent_id"] = pd.to_numeric(data["sent_id"])

In [ ]:
data.head()

sent_id                                               text   term  \
0     3121               But the staff was so horrible to us.  staff   
1     3121               But the staff was so horrible to us.          
2     2777  To be completely fair, the only redeeming fact...   food   
3     2777  To be completely fair, the only redeeming fact...          
4     2777  To be completely fair, the only redeeming fact...          

   term_from  term_to term_polarity                 category category_polarity  
0          8       13      negative                                             
1          0        0                                service          negative  
2         57       61      positive                                             
3          0        0                                   food          positive  
4          0        0                anecdotes/miscellaneous          negative

Below is a sample for each sentence, aspect_term_cat_list, which contains, sent_id, sentence_text, term_list and categories given. We shall use this data to build category prediction model.

In [ ]:
aspect_term_cat_list[:2]

[(3121, 'But the staff was so horrible to us.', ['staff'], ['service']),
 (2777,
  "To be completely fair, the only redeeming factor was the food, which was above average, but couldn't make up for all the other deficiencies of Teodora.",
  ['food'],
  ['food', 'anecdotes/miscellaneous'])]

In [ ]:
train_ner = pd.read_csv("/content/drive/MyDrive/publicis/train.csv", encoding='unicode_escape')
test_ner = pd.read_csv("/content/drive/MyDrive/publicis/test.csv", encoding='unicode_escape')

In [ ]:
term_polarity_data = data[data["term_polarity"] != ""]
term_polarity_data.shape
polarity_labels = list(set(term_polarity_data["term_polarity"].values))

In [ ]:
train_polarity = term_polarity_data[term_polarity_data["sent_id"].isin(set(train_ner["sent_id"].tolist()))]
test_polarity = term_polarity_data[term_polarity_data["sent_id"].isin(set(test_ner["sent_id"].tolist()))]
train_polarity.shape, test_polarity.shape

((2533, 8), (1160, 8))

We are create a term polarity data for each term present in a sentence. We augment the term at the end of sentnce, and its polarity as label

In [ ]:
train_polarity["text"] = train_polarity["text"] + " [SEP] " + train_polarity["term"]
test_polarity["text"] = test_polarity["text"] + " [SEP] " + test_polarity["term"]
train_polarity.shape, test_polarity.shape

<ipython-input-78-bbfceffdc083>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_polarity["text"] = train_polarity["text"] + " [SEP] " + train_polarity["term"]
<ipython-input-78-bbfceffdc083>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_polarity["text"] = test_polarity["text"] + " [SEP] " + test_polarity["term"]


((2533, 8), (1160, 8))

In [ ]:
train_polarity.rename(columns = {"term_polarity": "labels"}, inplace=True)
test_polarity.rename(columns = {"term_polarity": "labels"}, inplace=True)

<ipython-input-82-1a2717a1f86c>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_polarity.rename(columns = {"term_polarity": "labels"}, inplace=True)
<ipython-input-82-1a2717a1f86c>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_polarity.rename(columns = {"term_polarity": "labels"}, inplace=True)


In [ ]:
train_polarity.columns

Index(['sent_id', 'text', 'term', 'term_from', 'term_to', 'labels', 'category',
       'category_polarity'],
      dtype='object')

In [ ]:
new_train = train_polarity[["text", "labels"]]
new_test = test_polarity[["text", "labels"]]

In [ ]:
from simpletransformers.classification import ClassificationModel, ClassificationArgs


model_args = ClassificationArgs()
model_args.labels_list = polarity_labels

args={"save_eval_checkpoints": False,
      "save_steps": -1,
      "output_dir": "/content/drive/MyDrive/publicis/polarity",
      'overwrite_output_dir': True,
      "save_model_every_epoch": False,
      #'reprocess_input_data': True,
      "labels_list" :polarity_labels,
      'learning_rate': 5e-5,
      "train_batch_size": 16,'num_train_epochs': 15,"max_seq_length": 256, "gradient_accumulation_steps": 8}
model = ClassificationModel(
                    "roberta",
                    "j-hartmann/emotion-english-distilroberta-base",
                    num_labels=4,
                    args=args, ignore_mismatched_sizes=True
                )

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at j-hartmann/emotion-english-distilroberta-base and are newly initialized because the shapes did not match:
- classifier.out_proj.weight: found shape torch.Size([7, 768]) in the checkpoint and torch.Size([4, 768]) in the model instantiated
- classifier.out_proj.bias: found shape torch.Size([7]) in the checkpoint and torch.Size([4]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [5]:
#Training the Model

from sklearn.metrics import accuracy_score, f1_score
model.train_model(new_train,eval_data = new_test,acc=f1_score, )

In [ ]:
new_train.labels.value_counts()

labels
positive    1450
negative     566
neutral      457
conflict      60
Name: count, dtype: int64

In [ ]:
#Evaluating the Model
result, model_outputs, preds_list = model.eval_model(new_test)
print(result)

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/12 [00:00<?, ?it/s]

{'mcc': 0.6072179128890552, 'eval_loss': 0.8975777179002762}


Here, on the evaluation dataset, we got an **MCC (Matthews correlation coefficient) = 0.61,** closer to +1 is better, we have scope of improvement.


**Note:**

*Matthews correlation coefficient (**MCC**) is a metric used to evaluate the quality of binary (two-class) classifications. It takes into account true and false positives and negatives and is generally regarded as a balanced measure that can be used even if the classes are of very different sizes. The MCC returns a value between -1 and +1, where:*

*+1 indicates a perfect prediction*,

*0 indicates no better than random prediction*,

*-1 indicates total disagreement between prediction and observation*.

*MCC is particularly useful in cases where the dataset is imbalanced, providing a more informative score than accuracy or F1 score in such scenarios.*

In [ ]:
print("Term List: ", term_polarity)
print("Term Polarity: ", term_polarity)

Term List:  ['food', 'flavors', 'Thai cuisine']
Term Polarity:  {'food': 'positive', 'flavors': 'positive', 'Thai cuisine': 'positive'}


food
very delicious
service


In [ ]:
polarity_model.predict([test_sentence+" [SEP] "+ term])

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

(['positive'],
 array([[ 0.33496094, -0.61132812,  6.23046875, -0.03384399, -2.76171875,
         -2.0546875 , -2.15820312]]))

In [ ]:
# train

## Category Modelling

In [ ]:
# grouped_df = data.groupby('sent_id').agg({
#     'term': list,
#     'category': list,

# }).reset_index()

# print(grouped_df)

This is the (text, aspect-term and category) data we extracted from the xml in the previous steps

In [ ]:
aspect_term_cat_list[:3]

[(3121, 'But the staff was so horrible to us.', ['staff'], ['service']),
 (2777,
  "To be completely fair, the only redeeming factor was the food, which was above average, but couldn't make up for all the other deficiencies of Teodora.",
  ['food'],
  ['food', 'anecdotes/miscellaneous']),
 (1634,
  "The food is uniformly exceptional, with a very capable kitchen which will proudly whip up whatever you feel like eating, whether it's on the menu or not.",
  ['food', 'kitchen', 'menu'],
  ['food'])]

**Initially we shall work with cases of single category occurences, for example**
**we shall take data of those sentences, which looks like below:**

i.e having single category.
terms = ['food', 'kitchen', 'menu'],

category = ['food']

**We are ignoring the sentences, which has more than one category like:**

terms = ['food'],

category = ['food', 'anecdotes/miscellaneous'].


**Doing this we are losing some data, but including with will hinder the model performance, we shall explore the option of using the ignored data, once a base line model is built.**

In [ ]:
from collections import Counter
Counter([len(row[-1]) for row in aspect_term_cat_list])

Counter({1: 2465, 2: 486, 3: 84, 4: 6})

# As the multiple occurence of categories is ambigious to map, for the sake of time creating the data set with only single category

In [ ]:
# term_cat_dataset = [(row[0], row[1],  [row[-1][0]]*len(row[1])) for row in aspect_term_cat_list if (len(row[-1]) == 1 and len(row[-1][0]) > 0)]

We are creating a dataset for term category detection, here we are combining, sentence text with term as input sentence and the category as its label.

In [4]:
term_cat_dataset = []
for row in aspect_term_cat_list:
    sent_id, text, term_l, cat_l = row
    for ter in term_l:
        if len(cat_l) == 1:
            term_cat_dataset.append((sent_id, text + " [SEP] " + ter, cat_l[0]))
term_cat_dataset[:4]

In [ ]:
term_cat_df = pd.DataFrame(term_cat_dataset, columns=["sentence_id", "text", "labels"])
term_cat_df.head()

sentence_id                                               text   labels
0         3121   But the staff was so horrible to us. [SEP] staff  service
1         1634  The food is uniformly exceptional, with a very...     food
2         1634  The food is uniformly exceptional, with a very...     food
3         1634  The food is uniformly exceptional, with a very...     food
4         3161  The Bagels have an outstanding taste with a te...     food

In [ ]:
cat_labels = list(term_cat_df["labels"].value_counts().keys())

In [ ]:
# train and test data
train_cat = term_cat_df[term_cat_df["sentence_id"].isin(set(train_ner["sent_id"].tolist()))]
test_cat = term_cat_df[term_cat_df["sentence_id"].isin(set(test_ner["sent_id"].tolist()))]
train_cat.shape, test_cat.shape

((1700, 3), (777, 3))

In [ ]:
train_cat.labels.value_counts()

labels
food                       939
service                    340
ambience                   169
anecdotes/miscellaneous    165
price                       87
Name: count, dtype: int64

### Training Term Category Model

In [ ]:
#Training the Model
from simpletransformers.classification import ClassificationModel, ClassificationArgs


model_args = ClassificationArgs()
model_args.labels_list = polarity_labels

args={"save_eval_checkpoints": False,
      "save_steps": -1,
      "output_dir": "/content/drive/MyDrive/publicis/category",
      'overwrite_output_dir': True,
      "save_model_every_epoch": False,
      #'reprocess_input_data': True,
      "labels_list" :cat_labels,
      'learning_rate': 5e-5,
      "train_batch_size": 16,'num_train_epochs': 10,"max_seq_length": 256, "gradient_accumulation_steps": 8}
model = ClassificationModel(
                    "roberta",
                    "j-hartmann/emotion-english-distilroberta-base",
                    num_labels=5,
                    args=args, ignore_mismatched_sizes=True
                )


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at j-hartmann/emotion-english-distilroberta-base and are newly initialized because the shapes did not match:
- classifier.out_proj.weight: found shape torch.Size([7, 768]) in the checkpoint and torch.Size([5, 768]) in the model instantiated
- classifier.out_proj.bias: found shape torch.Size([7]) in the checkpoint and torch.Size([5]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [1]:
from sklearn.metrics import accuracy_score, f1_score
model.train_model(train_cat,eval_data = test_cat,acc=f1_score, )

In [2]:
#Evaluating the Model
result, model_outputs, preds_list = model.eval_model(test_cat)
print(result)

Here, on the evaluation dataset, we got an **MCC (Matthews correlation coefficient) = 0.84,** closer to +1 is better, we have scope of improvement.


**Note:**

*Matthews correlation coefficient (**MCC**) is a metric used to evaluate the quality of binary (two-class) classifications. It takes into account true and false positives and negatives and is generally regarded as a balanced measure that can be used even if the classes are of very different sizes. The MCC returns a value between -1 and +1, where:*

*+1 indicates a perfect prediction*,

*0 indicates no better than random prediction*,

*-1 indicates total disagreement between prediction and observation*.

*MCC is particularly useful in cases where the dataset is imbalanced, providing a more informative score than accuracy or F1 score in such scenarios.*

Inference:
- As we have all the 3 models trained, we need to get our desired outputs for a given sentence. Below is the code to run infernece on the sentence.

We follow few steps to perform inference:
1. **AspectNERModel**: Using the NER model for term or aspect, we shall get the aspect entites from the model, the below script is the post processing script to combine, mutli-word aspect entites into single aspect entity.
2. **AspectPolarityModel**: To know the polarity of the terms predicted from the above steps, we shall combine the sentence and term extracted and predict on this combined sentence, we get aspect specific polarity.
3. **AspectCategoryModel**: Finally to get the, term category, we shall combine the term extracted with the sentence and predict on this combined sentence, we get aspect specific category

In [ ]:
def combine_aspect_terms(token_list):
    combined_terms = []
    current_term = ""
    current_tag = ""

    for token_dict in token_list:
        token, tag = list(token_dict.items())[0]

        if tag == "B-ASPECT":
            if current_term:  # Save the current term before starting a new one
                combined_terms.append(current_term.strip())
            current_term = token + " "
            current_tag = "token"
        elif tag == "I-ASPECT" and current_tag == "token":
            current_term += token + " "
        else:
            if current_term:
                combined_terms.append(current_term.strip())
            current_term = ""
            current_tag = ""

    # Add the last term if there's any
    if current_term:
        combined_terms.append(current_term.strip())

    return combined_terms

In [ ]:
# !pip install simpletransformers

In [ ]:
from simpletransformers.ner import NERModel, NERArgs
from simpletransformers.classification import ClassificationModel, ClassificationArgs

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

Loading 3 models,
1. AspectNERModel
2. AspectPolarityModel
3. AspectCategoryModel

In [ ]:
aspect_model  = NERModel(
    "distilbert",
    "/content/drive/MyDrive/publicis/combined_ner",
ignore_mismatched_sizes=True, use_cuda=False, args={"slient": True}
)
polarity_model = ClassificationModel(
    "roberta",
    "/content/drive/MyDrive/publicis/polarity", ignore_mismatched_sizes=True, use_cuda=False,
    args={"slient": True},
)

category_model  = ClassificationModel(
    "roberta",
    "/content/drive/MyDrive/publicis/category", ignore_mismatched_sizes=True, use_cuda=False,
    args={"slient": True}
)

In [ ]:
def get_polarity(polarity_model, sentence, aspect_list):
    polarity_dict = []
    for aspect in aspect_list:
        polarity_dict.append(polarity_model.predict([sentence +" [SEP] "+ aspect])[0][0])
    return polarity_dict


def get_category(category_model, sentence, aspect_list):
    category_dict = []
    for aspect in aspect_list:
        category_dict.append(category_model.predict([sentence +" [SEP] "+ aspect])[0][0])
    return category_dict



In [ ]:

def gets_output_on_sentence(sentence):
    aspect_predictions, _ = aspect_model.predict([sentence])
    tokens_list = aspect_predictions[0]
    aspect_list_sent = combine_aspect_terms(tokens_list)
    aspect_polarity = get_polarity(polarity_model, sentence, aspect_list_sent)
    aspect_category = get_category(category_model, sentence, aspect_list_sent)
    return aspect_list_sent, aspect_polarity, aspect_category

In [ ]:
# sentence = """
# The food 's dazzling flavors overwhelm the palate , truly embracing the beauty of authentic Thai cuisine .
# """
# gets_output_on_sentence(sentence)

In [ ]:
data.head()

sent_id                                               text   term  \
0     3121               But the staff was so horrible to us.  staff   
1     3121               But the staff was so horrible to us.          
2     2777  To be completely fair, the only redeeming fact...   food   
3     2777  To be completely fair, the only redeeming fact...          
4     2777  To be completely fair, the only redeeming fact...          

   term_from  term_to term_polarity                 category category_polarity  
0          8       13      negative                                             
1          0        0                                service          negative  
2         57       61      positive                                             
3          0        0                                   food          positive  
4          0        0                anecdotes/miscellaneous          negative

In [ ]:
# ABSA Model Predictions on whole data

In [ ]:
unique_sentences = data.text.unique()

In [ ]:
import os
prediction_data = []
import json
for sent in unique_sentences:
    aspect_list_sent, aspect_polarity, aspect_category = gets_output_on_sentence(sent)
    for ent, pol, cat in zip(aspect_list_sent, aspect_polarity, aspect_category):

        if os.path.exists("/content/drive/MyDrive/publicis/ABSA_prediction_data.json"):
            prediction_data = json.load(open("/content/drive/MyDrive/publicis/ABSA_prediction_data.json", "r"))
            prediction_data.append((sent, ent, pol, cat))
            json.dump(prediction_data, open("/content/drive/MyDrive/publicis/ABSA_prediction_data.json", "w"))
        else:
            prediction_data.append((sent, ent, pol, cat))
            json.dump(prediction_data, open("/content/drive/MyDrive/publicis/ABSA_prediction_data.json", "w"))

json.dump(prediction_data, open("/content/drive/MyDrive/publicis/ABSA_prediction_data_final.json", "w"))

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

0it [00:00, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
import json
json.dump(prediction_data, open("/content/drive/MyDrive/publicis/ABSA_prediction_data.json", "w"))

aspect polarity category
0       NaN      NaN      NaN
1       NaN      NaN      NaN
2       NaN      NaN      NaN
3       NaN      NaN      NaN
4       NaN      NaN      NaN
...     ...      ...      ...
3030    NaN      NaN      NaN
3031    NaN      NaN      NaN
3032    NaN      NaN      NaN
3033    NaN      NaN      NaN
3034    NaN      NaN      NaN

[3035 rows x 3 columns]

In [3]:
# prediction_data